## Pandas Profiling: NASA Meteorites example
Source of data: https://data.nasa.gov/Space-Science/Meteorite-Landings/gh4g-9sfh

The autoreload instruction reloads modules automatically before code execution, which is helpful for the update below.

In [1]:
%load_ext autoreload
%autoreload 2

Make sure that we have the latest version of pandas-profiling.

In [2]:
import sys

!{sys.executable} -m pip install -U ydata-profiling[notebook]
!pip install jupyter-contrib-nbextensions
!jupyter nbextension enable --py widgetsnbextension

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 23.5/23.5 MB 7.1 MB/s eta 0:00:007.1 MB/s eta 0:00:01
  Preparing metadata (setup.py) ... done
  Preparing metadata (setup.py) ... done
  Created wheel for jupyter-contrib-nbextensions: filename=jupyter_contrib_nbextensions-0.7.0-py2.py3-none-any.whl size=23428776 sha256=173217d462a6d5be39fcd88c5ceaff72409bcaa82616fc2d4367b7ec460dc5b7
  Stored in directory: /home/zero/.cache/pip/wheels/4d/e4/20/dd16cdbbddcfe309a4559ea16adfa75fa5c554cfd076f9dae8
  Created wheel for jupyter_contrib_core: filename=jupyter_contrib_core-0.4.2-py2.py3-none-any.whl size=17480 sha256=4c55e537de7bb2b17d1b51b7ad100a91190edee222d6d63c02855c33eb95cb12
  Stored in directory: /home/zero/.cache/pip/wheels/32/f9/af/259a6f50f8b89d972aa81e31808a0af14e8bfc6867fb16ed07
Successfully built jupyter-contrib-nbextensions jupyter_contrib_core
usage: jupyter [-h] [--version] [--config-dir] [--data-dir] [--runtime-dir]
               [--paths] [--json] [--debug]
               [subcom

You might want to restart the kernel now.

### Import libraries

In [3]:
from pathlib import Path

import numpy as np
import pandas as pd
import requests

import ydata_profiling
from ydata_profiling.utils.cache import cache_file

### Load and prepare example dataset
We add some fake variables for illustrating pandas-profiling capabilities

In [4]:
file_name = cache_file(
    "meteorites.csv",
    "https://data.nasa.gov/api/views/gh4g-9sfh/rows.csv?accessType=DOWNLOAD",
)

df = pd.read_csv(file_name)

# Note: Pandas does not support dates before 1880, so we ignore these for this analysis
df["year"] = pd.to_datetime(df["year"], errors="coerce")

# Example: Constant variable
df["source"] = "NASA"

# Example: Boolean variable
df["boolean"] = np.random.choice([True, False], df.shape[0])

# Example: Mixed with base types
df["mixed"] = np.random.choice([1, "A"], df.shape[0])

# Example: Highly correlated variables
df["reclat_city"] = df["reclat"] + np.random.normal(scale=5, size=(len(df)))

# Example: Duplicate observations
duplicates_to_add = pd.DataFrame(df.iloc[0:10])
duplicates_to_add["name"] = duplicates_to_add["name"] + " copy"

df = pd.concat([df, duplicates_to_add], ignore_index=True)

### Inline report without saving object

In [5]:
report = df.profile_report(
    sort=None, html={"style": {"full_width": True}}, progress_bar=False
)
report

### Save report to file

In [6]:
profile_report = df.profile_report(html={"style": {"full_width": True}})
profile_report.to_file("/tmp/example.html")

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

/home/zero/miniconda3/lib/python3.12/site-packages/ydata_profiling/model/pandas/describe_date_pandas.py:44: UserWarning: Discarding nonzero nanoseconds in conversion.
  "min": pd.Timestamp.to_pydatetime(series.min()),
/home/zero/miniconda3/lib/python3.12/site-packages/ydata_profiling/model/pandas/describe_date_pandas.py:45: UserWarning: Discarding nonzero nanoseconds in conversion.
  "max": pd.Timestamp.to_pydatetime(series.max()),


Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

Export report to file:   0%|          | 0/1 [00:00<?, ?it/s]

### More analysis (Unicode) and Print existing ProfileReport object inline

In [7]:
profile_report = df.profile_report(
    explorative=True, html={"style": {"full_width": True}}
)
profile_report

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

### Notebook Widgets

In [8]:
profile_report.to_widgets()

Render widgets:   0%|          | 0/1 [00:00<?, ?it/s]

IOPub message rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_msg_rate_limit`.

Current values:
ServerApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
ServerApp.rate_limit_window=3.0 (secs)



boolean      fall        id  mass (g)     mixed  nametype  \
boolean      1.000000  0.000000  0.000000  0.000000  0.000000  0.000000   
fall         0.000000  1.000000  0.126388  0.012114  0.000000  0.000000   
id           0.000000  0.126388  1.000000 -0.141548  0.000000  0.129949   
mass (g)     0.000000  0.012114 -0.141548  1.000000  0.000000  0.000000   
mixed        0.000000  0.000000  0.000000  0.000000  1.000000  0.000000   
nametype     0.000000  0.000000  0.129949  0.000000  0.000000  1.000000   
reclat       0.000000  0.449923  0.261210  0.408746  0.004395  0.349340   
reclat_city  0.000000  0.400400  0.218883  0.421334  0.004599  0.335825   
reclong      0.008119  0.194729 -0.316046 -0.281372  0.010152  0.043965   

               reclat  reclat_city   reclong  
boolean      0.000000     0.000000  0.008119  
fall         0.449923     0.400400  0.194729  
id           0.261210     0.218883 -0.316046  
mass (g)     0.408746     0.421334 -0.281372  
mixed        0.004395     0.004599  0.010152  
nametype     0.349340     0.335825  0.043965  
reclat       1.000000     0.942890 -0.650308  
reclat_city  0.942890     1.000000 -0.616445  
reclong     -0.650308    -0.616445  1.000000

name   id nametype     recclass  mass (g)  fall  \
0               Aachen    1    Valid           L5      21.0  Fell   
1               Aarhus    2    Valid           H6     720.0  Fell   
2                 Abee    6    Valid          EH4  107000.0  Fell   
3             Acapulco   10    Valid  Acapulcoite    1914.0  Fell   
4              Achiras  370    Valid           L6     780.0  Fell   
5             Adhi Kot  379    Valid          EH4    4239.0  Fell   
6  Adzhi-Bogdo (stone)  390    Valid        LL3-6     910.0  Fell   
7                 Agen  392    Valid           H5   30000.0  Fell   
8               Aguada  398    Valid           L6    1620.0  Fell   
9        Aguila Blanca  417    Valid            L    1440.0  Fell   

                           year    reclat    reclong           GeoLocation  \
0 1970-01-01 00:00:00.000001880  50.77500    6.08333     (50.775, 6.08333)   
1 1970-01-01 00:00:00.000001951  56.18333   10.23333  (56.18333, 10.23333)   
2 1970-01-01 00:00:00.000001952  54.21667 -113.00000    (54.21667, -113.0)   
3 1970-01-01 00:00:00.000001976  16.88333  -99.90000     (16.88333, -99.9)   
4 1970-01-01 00:00:00.000001902 -33.16667  -64.95000   (-33.16667, -64.95)   
5 1970-01-01 00:00:00.000001919  32.10000   71.80000          (32.1, 71.8)   
6 1970-01-01 00:00:00.000001949  44.83333   95.16667  (44.83333, 95.16667)   
7 1970-01-01 00:00:00.000001814  44.21667    0.61667   (44.21667, 0.61667)   
8 1970-01-01 00:00:00.000001930 -31.60000  -65.23333    (-31.6, -65.23333)   
9 1970-01-01 00:00:00.000001920 -30.86667  -64.55000   (-30.86667, -64.55)   

  source  boolean mixed  reclat_city  
0   NASA    False     1    42.183688  
1   NASA    False     A    52.796155  
2   NASA    False     1    45.815963  
3   NASA     True     A     6.787124  
4   NASA     True     1   -38.757018  
5   NASA     True     A    32.429366  
6   NASA    False     A    55.180639  
7   NASA     True     A    41.814493  
8   NASA    False     A   -33.948820  
9   NASA    False     1   -26.273491

name   id nametype     recclass  mass (g)  fall  \
45716               Aachen copy    1    Valid           L5      21.0  Fell   
45717               Aarhus copy    2    Valid           H6     720.0  Fell   
45718                 Abee copy    6    Valid          EH4  107000.0  Fell   
45719             Acapulco copy   10    Valid  Acapulcoite    1914.0  Fell   
45720              Achiras copy  370    Valid           L6     780.0  Fell   
45721             Adhi Kot copy  379    Valid          EH4    4239.0  Fell   
45722  Adzhi-Bogdo (stone) copy  390    Valid        LL3-6     910.0  Fell   
45723                 Agen copy  392    Valid           H5   30000.0  Fell   
45724               Aguada copy  398    Valid           L6    1620.0  Fell   
45725        Aguila Blanca copy  417    Valid            L    1440.0  Fell   

                               year    reclat    reclong  \
45716 1970-01-01 00:00:00.000001880  50.77500    6.08333   
45717 1970-01-01 00:00:00.000001951  56.18333   10.23333   
45718 1970-01-01 00:00:00.000001952  54.21667 -113.00000   
45719 1970-01-01 00:00:00.000001976  16.88333  -99.90000   
45720 1970-01-01 00:00:00.000001902 -33.16667  -64.95000   
45721 1970-01-01 00:00:00.000001919  32.10000   71.80000   
45722 1970-01-01 00:00:00.000001949  44.83333   95.16667   
45723 1970-01-01 00:00:00.000001814  44.21667    0.61667   
45724 1970-01-01 00:00:00.000001930 -31.60000  -65.23333   
45725 1970-01-01 00:00:00.000001920 -30.86667  -64.55000   

                GeoLocation source  boolean mixed  reclat_city  
45716     (50.775, 6.08333)   NASA    False     1    42.183688  
45717  (56.18333, 10.23333)   NASA    False     A    52.796155  
45718    (54.21667, -113.0)   NASA    False     1    45.815963  
45719     (16.88333, -99.9)   NASA     True     A     6.787124  
45720   (-33.16667, -64.95)   NASA     True     1   -38.757018  
45721          (32.1, 71.8)   NASA     True     A    32.429366  
45722  (44.83333, 95.16667)   NASA    False     A    55.180639  
45723   (44.21667, 0.61667)   NASA     True     A    41.814493  
45724    (-31.6, -65.23333)   NASA    False     A   -33.948820  
45725   (-30.86667, -64.55)   NASA    False     1   -26.273491